In [ ]:
import numpy as np 
import pandas as pd 

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

/kaggle/input/resnet50/resnet50_weights_tf_dim_ordering_tf_kernels_notop.h5
/kaggle/input/cifar-10-object-recognition-resnet-acc-94/__results__.html
/kaggle/input/cifar-10-object-recognition-resnet-acc-94/__notebook__.ipynb
/kaggle/input/cifar-10-object-recognition-resnet-acc-94/__output__.json
/kaggle/input/cifar-10-object-recognition-resnet-acc-94/custom.css
/kaggle/input/cifar-10-object-recognition-resnet-acc-94/__results___files/__results___20_1.png
/kaggle/input/cifar-10-object-recognition-resnet-acc-94/__results___files/__results___18_1.png
/kaggle/input/cifar-10-object-recognition-resnet-acc-94/__results___files/__results___19_1.png
/kaggle/input/cifar-10-object-recognition-resnet-acc-94/__results___files/__results___27_0.png
/kaggle/input/cifar-10-object-recognition-resnet-acc-94/__results___files/__results___46_0.png
/kaggle/input/cifar-10-object-recognition-resnet-acc-94/__results___files/__results___51_0.png
/kaggle/input/cifar-10-object-recognition-resnet-acc-94/__results__

In [2]:
import os
import numpy as np
import pickle
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers, models

dataset_path = "/kaggle/input/cifar-10-python-tar/cifar-10-batches-py"
weights_path = "/kaggle/input/resnet50/resnet50_weights_tf_dim_ordering_tf_kernels_notop.h5"


def load_cifar_batch(filename):
    with open(filename, 'rb') as f:
        data_dict = pickle.load(f, encoding='bytes')
        images = data_dict[b'data']
        labels = data_dict[b'labels']
        images = images.reshape(len(images), 3, 32, 32).transpose(0, 2, 3, 1)
        return images, labels

# Loading training batches
x_train, y_train = [], []
for i in range(1, 6):
    images, labels = load_cifar_batch(os.path.join(dataset_path, f'data_batch_{i}'))
    x_train.append(images)
    y_train.extend(labels)

x_train = np.concatenate(x_train)
y_train = np.array(y_train)

# Loading test batch
x_test, y_test = load_cifar_batch(os.path.join(dataset_path, 'test_batch'))
y_test = np.array(y_test)

print("Full Train:", x_train.shape, y_train.shape)
print("Full Test:", x_test.shape, y_test.shape)


subset_fraction = 0.3
subset_size = int(len(x_train) * subset_fraction)

indices = np.random.choice(len(x_train), subset_size, replace=False)
x_train = x_train[indices]
y_train = y_train[indices]

print(f"Subset: {x_train.shape}, {y_train.shape}")


#  Normalize & One-hot encode

x_train = x_train.astype("float32") / 255.0
x_test = x_test.astype("float32") / 255.0

num_classes = 10
y_train_cat = keras.utils.to_categorical(y_train, num_classes)
y_test_cat = keras.utils.to_categorical(y_test, num_classes)


#  MixUp augmentation

def mixup(batch_x, batch_y, alpha=0.2):
    lam = np.random.beta(alpha, alpha)
    batch_size = batch_x.shape[0]
    index = np.random.permutation(batch_size)
    mixed_x = lam * batch_x + (1 - lam) * batch_x[index]
    mixed_y = lam * batch_y + (1 - lam) * batch_y[index]
    return mixed_x, mixed_y

class MixupGenerator(keras.utils.Sequence):
    def __init__(self, x, y, batch_size=64, alpha=0.2):
        self.x = x
        self.y = y
        self.batch_size = batch_size
        self.alpha = alpha
        self.indices = np.arange(len(x))

    def __len__(self):
        return len(self.x) // self.batch_size

    def __getitem__(self, idx):
        batch_ids = np.random.choice(self.indices, self.batch_size)
        batch_x = self.x[batch_ids]
        batch_y = self.y[batch_ids]
        return mixup(batch_x, batch_y, self.alpha)

mixup_train_gen = MixupGenerator(x_train, y_train_cat, batch_size=64, alpha=0.2)


# Build ResNet50 model

base_model = tf.keras.applications.ResNet50(
    include_top=False,
    weights=None,
    input_shape=(32, 32, 3),
    pooling='avg'
)
base_model.load_weights(weights_path)

model = models.Sequential([
    base_model,
    layers.Dense(256, activation='relu'),
    layers.Dropout(0.5),
    layers.Dense(num_classes, activation='softmax')
])

model.compile(
    optimizer=keras.optimizers.Adam(learning_rate=5e-4),
    loss='categorical_crossentropy',
    metrics=['accuracy']
)


# Train model

history = model.fit(
    mixup_train_gen,
    validation_data=(x_test, y_test_cat),
    epochs=5,
    verbose=1
)


# Final evaluation

val_loss, val_acc = model.evaluate(x_test, y_test_cat, verbose=0)
print(f"\nFinal Validation Accuracy: {val_acc:.4f}")


2025-08-16 15:19:28.923723: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1755357569.154077      36 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1755357569.221804      36 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


Full Train: (50000, 32, 32, 3) (50000,)
Full Test: (10000, 32, 32, 3) (10000,)
Subset: (15000, 32, 32, 3), (15000,)


2025-08-16 15:19:47.124559: E external/local_xla/xla/stream_executor/cuda/cuda_driver.cc:152] failed call to cuInit: INTERNAL: CUDA error: Failed call to cuInit: UNKNOWN ERROR (303)


Epoch 1/5


/usr/local/lib/python3.11/dist-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


234/234 ━━━━━━━━━━━━━━━━━━━━ 660s 3s/step - accuracy: 0.3218 - loss: 2.3156 - val_accuracy: 0.1000 - val_loss: 2.8584
Epoch 2/5
234/234 ━━━━━━━━━━━━━━━━━━━━ 587s 3s/step - accuracy: 0.6211 - loss: 1.3685 - val_accuracy: 0.0999 - val_loss: 3.1804
Epoch 3/5
234/234 ━━━━━━━━━━━━━━━━━━━━ 585s 3s/step - accuracy: 0.7095 - loss: 1.1618 - val_accuracy: 0.1783 - val_loss: 2.6794
Epoch 4/5
234/234 ━━━━━━━━━━━━━━━━━━━━ 586s 3s/step - accuracy: 0.7500 - loss: 1.0423 - val_accuracy: 0.6132 - val_loss: 1.1822
Epoch 5/5
234/234 ━━━━━━━━━━━━━━━━━━━━ 587s 3s/step - accuracy: 0.7868 - loss: 0.8915 - val_accuracy: 0.7125 - val_loss: 0.8875

Final Validation Accuracy: 0.7125


In [3]:
model.save("resnet50_cifar10_subset.h5")


In [4]:
from sklearn.metrics import confusion_matrix, classification_report
import numpy as np

y_pred = np.argmax(model.predict(x_test, batch_size=256), axis=1)
y_true = np.argmax(y_test_cat, axis=1)
print(confusion_matrix(y_true, y_pred))
print(classification_report(y_true, y_pred))


40/40 ━━━━━━━━━━━━━━━━━━━━ 21s 443ms/step
[[792  16  77  17  16   4   2  13  33  30]
 [ 22 886   7   5   1   3   4   6   8  58]
 [ 53  11 748  38  54  52  14  17   3  10]
 [ 17  28 118 472  56 216  26  44   6  17]
 [ 33   6 130  71 608  61  19  63   3   6]
 [ 14   8  93 118  26 678   6  46   4   7]
 [  9  28  99  99  40  58 655   8   2   2]
 [ 15   9  45  29  52  63   1 774   2  10]
 [110  32  12  15  12   6   8   3 756  46]
 [ 35 131   7  19   2   5   6  24  15 756]]
              precision    recall  f1-score   support

           0       0.72      0.79      0.75      1000
           1       0.77      0.89      0.82      1000
           2       0.56      0.75      0.64      1000
           3       0.53      0.47      0.50      1000
           4       0.70      0.61      0.65      1000
           5       0.59      0.68      0.63      1000
           6       0.88      0.66      0.75      1000
           7       0.78      0.77      0.77      1000
           8       0.91      0.76      0